#### Data Extraction

Load CSV filed from DBFS

In [0]:
# import necessary libraries and functions
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("Delta Tables").getOrCreate()
from pyspark.sql import functions as F
from pyspark.sql.types import DateType, StringType, IntegerType, DoubleType, TimestampType

from datetime import datetime, timedelta

In [0]:
#loading csv files
payments_df = spark.read.format("csv").option("separator", ",").load('dbfs:/FileStore/tables/payments.csv')
ridrs_df = spark.read.format("csv").option("separator", ",").load('dbfs:/FileStore/tables/riders.csv')
staions_df = spark.read.format("csv").option("separator", ",").load('dbfs:/FileStore/tables/stations.csv')
trips_df = spark.read.format("csv").option("separator", ",").load('dbfs:/FileStore/tables/trips.csv')
display(payments_df.head(5))

_c0 _c1 _c2 _c3 1 2019-05-01 9.0 1000 2 2019-06-01 9.0 1000 3 2019-07-01 9.0 1000 4 2019-08-01 9.0 1000 5 2019-09-01 9.0 1000

In [0]:
payments_df = payments_df \
    .withColumnRenamed("_c0", "payment_id") \
    .withColumnRenamed("_c1", "date") \
    .withColumnRenamed("_c2", "amount") \
    .withColumnRenamed("_c3", "rider_id")


payments_df = payments_df \
    .withColumn("payment_id", F.col("payment_id").cast(IntegerType())) \
    .withColumn("date", F.col("date").cast(DateType())) \
    .withColumn("amount", F.col("amount").cast(DoubleType())) \
    .withColumn("rider_id", F.col("rider_id").cast(IntegerType()))

display(payments_df.head(5))


payment_id date amount rider_id 1 2019-05-01 9.0 1000 2 2019-06-01 9.0 1000 3 2019-07-01 9.0 1000 4 2019-08-01 9.0 1000 5 2019-09-01 9.0 1000

In [0]:
display(staions_df.head(5))

_c0 _c1 _c2 _c3 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

In [0]:
riders_df = ridrs_df.withColumnRenamed("_c0", "rider_id")\
                    .withColumnRenamed("_c1", "first_name")\
                    .withColumnRenamed("_c2", "last_name") \
                    .withColumnRenamed("_c3", "address")\
                    .withColumnRenamed("_c4", "birthday") \
                    .withColumnRenamed("_c5", "account_start_date") \
                    .withColumnRenamed("_c6", "account_end_date")\
                    .withColumnRenamed("_c7", "IsMember") 

riders_df = riders_df.withColumn("rider_id", F.col("rider_id").cast(IntegerType()))\
                     .withColumn("birthday", F.col("birthday").cast(DateType()))\
                     .withColumn("account_start_date", F.col("account_start_date").cast(DateType()))\
                     .withColumn("account_end_date", F.col("account_end_date").cast(DateType()))\
                     .withColumn("age", (F.datediff(F.col("account_start_date"), F.col("birthday")) / 365).cast('int'))\
                     .withColumn("IsMember", F.when(F.col("IsMember") == "True","Rider").otherwise("Casual"))
                    

display(riders_df.head(5))

rider_id first_name last_name address birthday account_start_date account_end_date IsMember age 1000 Diana Clark 1200 Alyssa Squares 1989-02-13 2019-04-23 null True 30 1001 Jennifer Smith 397 Diana Ferry 1976-08-10 2019-11-01 2020-09-01 True 43 1002 Karen Smith 644 Brittany Row Apt. 097 1998-08-10 2022-02-04 null True 23 1003 Bryan Roberts 996 Dickerson Turnpike 1999-03-29 2019-08-26 null False 20 1004 Jesse Middleton 7009 Nathan Expressway 1969-04-11 2019-09-14 null True 50

In [0]:
display(riders_df.head(5))


rider_id first_name last_name address birthday account_start_date account_end_date IsMember age 1000 Diana Clark 1200 Alyssa Squares 1989-02-13 2019-04-23 null Rider 30 1001 Jennifer Smith 397 Diana Ferry 1976-08-10 2019-11-01 2020-09-01 Rider 43 1002 Karen Smith 644 Brittany Row Apt. 097 1998-08-10 2022-02-04 null Rider 23 1003 Bryan Roberts 996 Dickerson Turnpike 1999-03-29 2019-08-26 null Casual 20 1004 Jesse Middleton 7009 Nathan Expressway 1969-04-11 2019-09-14 null Rider 50

In [0]:
staions_df = staions_df.withColumnRenamed("_c0", "station_id")\
                       .withColumnRenamed("_c1", "name")\
                        .withColumnRenamed("_c2", "latitude")\
                        .withColumnRenamed("_c3", "longitude")

staions_df = staions_df.withColumn("latitude", F.col("latitude").cast(DoubleType()))\
                       .withColumn("longitude", F.col("longitude").cast(DoubleType()))

display(staions_df.head(5))

station_id name latitude longitude 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669

In [0]:
display(trips_df.head(5))

_c0 _c1 _c2 _c3 _c4 _c5 _c6 89E7AA6C29227EFF classic_bike 2021-02-12 16:14:56 2021-02-12 16:21:43 525 660 71934 0FEFDE2603568365 classic_bike 2021-02-14 17:52:38 2021-02-14 18:12:09 525 16806 47854 E6159D746B2DBB91 electric_bike 2021-02-09 19:10:18 2021-02-09 19:19:10 KA1503000012 TA1305000029 70870 B32D3199F1C2E75B classic_bike 2021-02-02 17:49:41 2021-02-02 17:54:06 637 TA1305000034 58974 83E463F23575F4BF electric_bike 2021-02-23 15:07:23 2021-02-23 15:22:37 13216 TA1309000055 39608

In [0]:
trips_df = trips_df.withColumnRenamed("_c0", "trip_id")\
                   .withColumnRenamed("_c1", "bike_type")\
                    .withColumnRenamed("_c2", "start_at")\
                     .withColumnRenamed("_c3", "end_at")\
                      .withColumnRenamed("_c4", "start_station_id")\
                       .withColumnRenamed("_c5", "end_station_id")\
                        .withColumnRenamed("_c6", "rider_id")

trips_df = trips_df.withColumn("start_at", F.col("start_at").cast(TimestampType()))\
                   .withColumn("end_at", F.col("end_at").cast(TimestampType()))\
                    .withColumn("rider_id", F.col("rider_id").cast(IntegerType()))\
                    .withColumn('duration_mins', ((F.unix_timestamp(F.col('end_at')) - F.unix_timestamp(F.col('start_at'))) / 60))\
                    .withColumn("duration_mins", F.round(F.col("duration_mins"), 2))

display(trips_df.head(5))               
                   

trip_id bike_type start_at end_at start_station_id end_station_id rider_id duration_mins 89E7AA6C29227EFF classic_bike 2021-02-12T16:14:56Z 2021-02-12T16:21:43Z 525 660 71934 6.78 0FEFDE2603568365 classic_bike 2021-02-14T17:52:38Z 2021-02-14T18:12:09Z 525 16806 47854 19.52 E6159D746B2DBB91 electric_bike 2021-02-09T19:10:18Z 2021-02-09T19:19:10Z KA1503000012 TA1305000029 70870 8.87 B32D3199F1C2E75B classic_bike 2021-02-02T17:49:41Z 2021-02-02T17:54:06Z 637 TA1305000034 58974 4.42 83E463F23575F4BF electric_bike 2021-02-23T15:07:23Z 2021-02-23T15:22:37Z 13216 TA1309000055 39608 15.23

Tranformation of Data

## Creating delta tables 


In [0]:

tables = ["fact_trips", "fact_payments", "dim_riders", "dim_stations", "dim_date"]

for table in tables:
    spark.sql(f"DROP TABLE IF EXISTS {table}")

In [0]:
trips_df.write.format("delta").mode("overwrite").saveAsTable("fact_trips")
riders_df.write.format("delta").mode("overwrite").saveAsTable("dim_riders")
staions_df.write.format("delta").mode("overwrite").saveAsTable("dim_stations")
payments_df.write.format("delta").mode("overwrite").saveAsTable("fact_payments")          

In [0]:
row = spark.sql("SELECT MIN(start_at) AS min_ts, MAX(start_at) AS max_ts FROM fact_trips").collect()[0]
min_date = row['min_ts'].date()
max_date = row['max_ts'].date()

num_hours = int(((max_date - min_date).days + 1) * 24)


#date_df = spark.range(0, num_hours).withColumn("full_datetime", F.expr(f"CAST('{min_date}' AS TIMESTAMP) + INTERVAL id HOUR")).drop("id")
date_df = spark.range(0, num_hours).withColumn("full_datetime",F.expr(f"timestamp('{min_date}') + id * interval 1 second * 3600")).drop("id")


dim_date = date_df.withColumn("date", F.date_format("full_datetime", "yyyy-MM-dd").cast(DateType()))\
                   .withColumn("year", F.year(F.col("date")))\
                   .withColumn("month", F.month(F.col("date")))\
                   .withColumn("day", F.dayofmonth(F.col("date")))\
                   .withColumn("qtr", F.quarter(F.col("date")))\
                   .withColumn("week", F.weekofyear(F.col("date")))\
                    .withColumn('day_of_the_week', F.dayofweek(F.col("date")))\
                   .withColumn("hour", F.date_format("full_datetime", "HH"))\
                    .withColumn("time_of_the_day",F.when((F.col("hour") >= 5) & (F.col("hour") <= 11), "morning")\
                        .when((F.col("hour") >= 12) & (F.col("hour") <= 16), "afternoon")\
                            .when((F.col("hour") >= 17) & (F.col("hour") <= 21), "evening").otherwise("night"))

                  
                                            
dim_date.limit(5).display()

full_datetime date year month day qtr week day_of_the_week hour time_of_the_day 2021-02-01T00:00:00Z 2021-02-01 2021 2 1 1 5 2 00 night 2021-02-01T01:00:00Z 2021-02-01 2021 2 1 1 5 2 01 night 2021-02-01T02:00:00Z 2021-02-01 2021 2 1 1 5 2 02 night 2021-02-01T03:00:00Z 2021-02-01 2021 2 1 1 5 2 03 night 2021-02-01T04:00:00Z 2021-02-01 2021 2 1 1 5 2 04 night

In [0]:
dim_date.write.format("delta").mode("overwrite").saveAsTable("dim_date")

## Business Outcomes Analysis 

#  The business outcomes you are designing for:

##  Analyze how much time is spent per ride
- 
- Based on date and time factors such as day of week and time of day
- Based on which station is the starting and / or ending station
- Based on age of the rider at time of the ride
- Based on whether the rider is a member or a casual rider

In [0]:
trips_df = spark.table('fact_trips')
riders_df = spark.table('dim_riders')
stations_df = spark.table('dim_stations')
date_df = spark.table('dim_date')
payments_df = spark.table('fact_payments')

**Based on date and time factors such as day of week and time of day**

In [0]:
#how much time is spent per ride Based on date and time factors such as day of week and time of day

trips_df = trips_df.withColumn("start_date", F.to_date(F.col("start_at")))

riders_time_df = trips_df.join(date_df, [F.col('start_date') == F.col('date')], how = 'left') \
                         .groupBy('rider_id', 'day_of_the_week', 'time_of_the_day') \
                         .agg(F.sum('duration_mins').alias('total_time_spent_mins')).orderBy('rider_id')
display(riders_time_df)

rider_id day_of_the_week time_of_the_day total_time_spent_mins 1000 1 night 448.0 1000 5 night 467.2499999999999 1000 7 evening 235.05 1000 1 morning 448.0 1000 6 night 436.94 1000 3 evening 193.04999999999998 1000 1 evening 320.0 1000 4 morning 602.5600000000001 1000 1 afternoon 320.0 1000 5 morning 467.2499999999999 1000 5 afternoon 333.74999999999994 1000 4 afternoon 430.4 1000 4 evening 430.4 1000 7 night 329.07000000000005 1000 7 morning 329.07000000000005 1000 6 morning 436.94 1000 6 evening 312.1 1000 3 night 270.27 1000 4 night 602.5600000000001 1000 3 morning 270.27 1000 6 afternoon 312.1 1000 7 afternoon 235.05 1000 3 afternoon 193.04999999999998 1000 5 evening 333.74999999999994 1002 4 morning 64.05 1002 4 evening 45.75 1002 4 afternoon 45.75 1002 4 night 64.05 1003 5 morning 1828.0500000000004 1003 1 afternoon 1655.7999999999995 1003 4 night 3055.3599999999997 1003 6 night 1670.06 1003 5 afternoon 1305.7500000000002 1003 7 evening 2097.95 1003 2 evening 605.3 1003 2 morning 847.4200000000001 1003 6 afternoon 1192.9 1003 5 night 1828.0500000000004 1003 3 evening 1062.0000000000002 1003 4 evening 2182.4 1003 6 evening 1192.9 1003 3 afternoon 1062.0000000000002 1003 4 morning 3055.3599999999997 1003 1 evening 1655.7999999999995 1003 4 afternoon 2182.4 1003 1 morning 2318.12 1003 5 evening 1305.7500000000002 1003 2 afternoon 605.3 1003 7 morning 2937.130000000001 1003 1 night 2318.12 1003 7 afternoon 2097.95 1003 3 morning 1486.8000000000002 1003 3 night 1486.8000000000002 1003 2 night 847.4200000000001 1003 6 morning 1670.06 1003 7 night 2937.130000000001 1006 4 night 2662.3100000000004 1006 4 morning 2662.3100000000004 1006 6 morning 1218.21 1006 4 afternoon 1901.6500000000005 1006 1 night 4147.079999999999 1006 6 evening 870.15 1006 5 night 1837.9200000000008 1006 3 morning 3002.0900000000015 1006 7 morning 4396.0 1006 7 night 4396.0 1006 3 night 3002.0900000000015 1006 7 evening 3140.0000000000005 1006 5 evening 1312.8000000000006 1006 3 evening 2144.3500000000004 1006 2 evening 925.7500000000002 1006 3 afternoon 2144.3500000000004 1006 6 afternoon 870.15 1006 5 morning 1837.9200000000008 1006 1 morning 4147.079999999999 1006 2 night 1296.05 1006 7 afternoon 3140.0000000000005 1006 2 morning 1296.05 1006 1 evening 2962.2 1006 1 afternoon 2962.2 1006 4 evening 1901.6500000000005 1006 6 night 1218.21 1006 5 afternoon 1312.8000000000006 1006 2 afternoon 925.7500000000002 1007 4 afternoon 2160.25 1007 3 afternoon 1843.4499999999998 1007 6 night 1924.6500000000003 1007 7 night 2761.99 1007 5 evening 1439.0 1007 2 night 2714.3200000000006 1007 6 evening 1374.7500000000005 1007 1 night 3760.6800000000007 1007 1 evening 2686.2 1007 4 morning 3024.349999999998 1007 7 evening 1972.8499999999995 1007 6 morning 1924.6500000000003 1007 4 evening 2160.25 1007 1 afternoon 2686.2 1007 5 afternoon 1439.0 1007 2 morning 2714.3200000000006 1007 3 morning 2580.8300000000004 1007 2 evening 1938.7999999999997 1007 5 morning 2014.6000000000001 1007 2 afternoon 1938.7999999999997 1007 5 night 2014.6000000000001 1007 7 morning 2761.99 1007 4 night 3024.349999999998 1007 1 morning 3760.6800000000007 1007 3 evening 1843.4499999999998 1007 3 night 2580.8300000000004 1007 7 afternoon 1972.8499999999995 1007 6 afternoon 1374.7500000000005 1008 1 evening 4987.600000000001 1008 2 afternoon 2527.4499999999994 1008 7 night 4741.379999999998 1008 3 night 5264.490000000002 1008 3 evening 3760.3500000000013 1008 1 afternoon 4987.600000000001 1008 4 afternoon 2309.0 1008 1 morning 6982.640000000003 1008 7 afternoon 3386.6999999999985 1008 5 morning 2447.2700000000004 1008 5 afternoon 1748.0500000000002 1008 5 night 2447.2700000000004 1008 5 evening 1748.0500000000002 1008 2 evening 2527.4499999999994 1008 2 morning 3538.43 1008 6 morning 3957.450000000004 1008 7 morning 4741.379999999998 1008 6 afternoon 2826.750000000002 1008 3 afternoon 3760.3500000000013 1008 3 morning 5264.490000000002 1008 1 night 6982.640000000003 1008 4 evening 2309.0 1008 7 eve

In [0]:
trips_df.join(date_df, (F.col('start_date') == F.col('date')), how = 'left').groupBy('day_of_the_week').agg(F.sum('duration_mins').alias('total_duration_mins'),
                                                                                                            F.avg('duration_mins').alias('avg_duration_mins')).orderBy('day_of_the_week').display()

day_of_the_week total_duration_mins avg_duration_mins 1 4.7649294839996505E8 27.8250166777364 2 2.8514334384002113E8 20.62292925768893 3 2.6382919296004564E8 18.176754473139525 4 2.6678096904003495E8 18.035412031751278 5 2.619418036799556E8 18.24242434675909 6 3.2627665896002436E8 20.805764135669687 7 5.170552423199687E8 26.194230099576515

In [0]:
trips_df.join(date_df, (F.col('start_date') == F.col('date')), how = 'left').groupBy('time_of_the_day').agg(F.sum('duration_mins').alias('total_duration_mins'),
                                                                                                            F.count('*').alias('total_trips')).display()

time_of_the_day total_duration_mins total_trips afternoon 4.99483366500005E8 22924605 night 6.992767130999637E8 32094447 morning 6.992767130999637E8 32094447 evening 4.99483366500005E8 22924605

In [0]:
trips_df.join(date_df, (F.col('start_date') == F.col('date')), how = 'left').groupBy('day_of_the_week', 'time_of_the_day').agg(F.sum('duration_mins').alias('total_duration_mins'),
                                                                                                            F.avg('duration_mins').alias('avg_duration_mins'),
                                                                                                            F.count('*').alias('total_trips')).orderBy('day_of_the_week').display()

day_of_the_week time_of_the_day total_duration_mins avg_duration_mins total_trips 1 morning 1.389771099500025E8 27.82501667773894 4994682 1 evening 9.926936425000381E7 27.825016677739512 3567630 1 night 1.389771099500025E8 27.82501667773894 4994682 1 afternoon 9.926936425000381E7 27.825016677739512 3567630 2 night 8.316680861999758E7 20.6229292576868 4032735 2 afternoon 5.940486329999884E7 20.622929257686998 2880525 2 evening 5.940486329999884E7 20.622929257686998 2880525 2 morning 8.316680861999756E7 20.622929257686796 4032735 3 morning 7.695018128000076E7 18.17675447313656 4233439 3 evening 5.496441519999855E7 18.1767544731359 3023885 3 afternoon 5.496441519999855E7 18.1767544731359 3023885 3 night 7.695018128000076E7 18.17675447313656 4233439 4 night 7.781111596999986E7 18.035412031748884 4314352 4 afternoon 5.5579368550001256E7 18.035412031749324 3081680 4 morning 7.781111596999986E7 18.035412031748884 4314352 4 evening 5.5579368550001256E7 18.035412031749324 3081680 5 morning 7.639969274000366E7 18.24242434676306 4188023 5 night 7.639969274000366E7 18.24242434676306 4188023 5 evening 5.457120910000116E7 18.24242434676257 2991445 5 afternoon 5.457120910000116E7 18.24242434676257 2991445 6 evening 6.797430394999969E7 20.80576413566804 3267090 6 night 9.516402553000471E7 20.80576413566916 4573926 6 morning 9.516402553000471E7 20.80576413566916 4573926 6 afternoon 6.797430394999969E7 20.80576413566804 3267090 7 afternoon 1.077198421500035E8 26.19423009957895 4112350 7 morning 1.5080777900999796E8 26.194230099577748 5757290 7 evening 1.077198421500035E8 26.19423009957895 4112350 7 night 1.5080777900999796E8 26.194230099577748 5757290

**Based on which station is the starting and / or ending station**

In [0]:
trips_df.join(stations_df, (F.col('start_station_id') == F.col('station_id')), how='left').groupBy('name').agg(F.count('*').alias('total_trips'), F.sum('duration_mins').alias
                                                                                                               ('total_duration_mins'), F.avg('duration_mins').alias('avg_duration_mins')).orderBy(F.desc('total_trips')).display()



name total_trips total_duration_mins avg_duration_mins Streeter Dr & Grand Ave 80344 3131935.6100000036 38.98157435527237 Lake Shore Dr & North Blvd 46380 1353331.0300000014 29.17919426476933 Lake Shore Dr & Monroe St 44672 1782985.4800000035 39.91281966332386 Michigan Ave & Oak St 42722 1551938.8199999968 36.32645522213372 Wells St & Concord Ln 41604 659284.11 15.84665200461494 Millennium Park 40505 1955578.3599999975 48.27992494753728 Clark St & Elm St 39346 686051.9300000005 17.43638311391248 Wells St & Elm St 35955 499983.4299999996 13.90581087470448 Theater on the Lake 35704 1044941.9500000007 29.266803439390564 Kingsbury St & Kinzie St 32422 385063.9899999993 11.87662667324654 Clark St & Lincoln Ave 31901 632543.8999999994 19.82834080436348 Clark St & Armitage Ave 31332 599959.4399999997 19.1484565300651 Wabash Ave & Grand Ave 31306 890235.8500000003 28.436588832811612 Dearborn St & Erie St 30271 542618.9299999999 17.925371808001056 Wells St & Huron St 29602 395972.8399999998 13.376556989392602 Broadway & Barry Ave 28980 508484.9199999999 17.54606349206349 St. Clair St & Erie St 28497 678278.7000000004 23.80175807979789 Indiana Ave & Roosevelt Rd 28382 886862.7199999983 31.247365231484686 Shedd Aquarium 27422 1001701.8399999996 36.529131354386976 Larrabee St & Webster Ave 26661 441490.6199999991 16.559417126139273 Wilton Ave & Belmont Ave 26237 473906.7100000001 18.06253420741701 New St & Illinois St 26071 703640.6700000003 26.989400866863576 Green St & Madison St 25748 408219.8700000001 15.85443024700948 Wells St & Evergreen Ave 25550 391722.93000000017 15.331621526418793 Fairbanks Ct & Grand Ave 25191 661391.9900000003 26.255090706998544 Michigan Ave & Lake St 24729 806794.7099999974 32.62544825912885 Desplaines St & Kinzie St 24544 326270.6900000007 13.293297343546312 Michigan Ave & Washington St 24369 802872.089999999 32.94645204973528 Clark St & Wrightwood Ave 24160 418269.87000000017 17.312494619205307 Lakeview Ave & Fullerton Pkwy 24157 506384.50000000023 20.96222626981828 LaSalle St & Illinois St 24088 467976.13000000024 19.42777025905016 Clinton St & Madison St 23953 362635.7400000003 15.13947062998373 Ashland Ave & Division St 23757 389916.41000000003 16.412695626552175 Wells St & Hubbard St 23677 369224.7400000006 15.594236600920748 Dearborn Pkwy & Delaware Pl 23164 404439.8399999997 17.459844586427202 Lincoln Ave & Fullerton Ave 23151 375613.5799999995 16.224507796639433 Clark St & Drummond Pl 22842 380997.86999999976 16.679707118465974 Columbus Dr & Randolph St 22754 594902.0899999996 26.144945504087175 Wabash Ave & Roosevelt Rd 22370 557397.3400000014 24.91718104604387 Lake Shore Dr & Diversey Pkwy 21897 547921.5900000009 25.022678449102656 Clark St & Newport St 21846 400953.80000000034 18.353648265128644 Clark St & Schiller St 21818 367063.49000000017 16.823883490695763 Lake Shore Dr & Wellington Ave 21575 505502.52000000054 23.430012514484382 Halsted St & Roscoe St 21438 380274.9400000005 17.738358988711656 Lake Shore Dr & Belmont Ave 21414 547093.6599999991 25.54841038572892 Lake Shore Dr & Ohio St 20684 842971.3799999994 40.754756333397765 Broadway & Cornelia Ave 20499 372716.43999999954 18.182176691545905 Broadway & Waveland Ave 20480 336458.1600000003 16.428621093750017 State St & Kinzie St 20213 517651.5300000009 25.609831791421406 Damen Ave & Pierce Ave 20206 368578.49999999977 18.241042264673847 Green St & Randolph St 20195 358507.3799999996 17.752284228769476 McClurg Ct & Erie St 20124 477425.8499999998 23.72420244484197 Rush St & Cedar St 20068 399829.9399999996 19.923756228821986 Clinton St & Washington Blvd 20052 281924.2399999997 14.059656892080575 Dusable Harbor 20039 947083.2799999986 47.2620030939667 Rush St & Superior St 19659 440393.4600000003 22.401620631771724 Pine Grove Ave & Waveland Ave 19591 416276.03999999934 21.24833035577558 State St & Randolph St 19492 489554.73999999964 25.11567514877897 Kingsbury St & Erie St 19426 231269.37999999995 11.905146710594046 Montrose Harbor 19289 67

In [0]:
trips_df.join(stations_df, (F.col('end_station_id') == F.col('station_id')), how='left').groupBy('name').agg(F.count('*').alias('total_trips'), F.sum('duration_mins').alias
                                                                                                               ('total_duration_mins'), F.avg('duration_mins').alias('avg_duration_mins')).orderBy(F.desc('total_trips')).display()

name total_trips total_duration_mins avg_duration_mins Streeter Dr & Grand Ave 81840 3144348.2600000054 38.42067766373418 Lake Shore Dr & North Blvd 52641 1488567.5700000012 28.277722117740947 Michigan Ave & Oak St 43435 1504248.359999997 34.63217129043392 Lake Shore Dr & Monroe St 43151 1651356.7000000016 38.2692567959028 Wells St & Concord Ln 41947 647914.3300000014 15.446023076739728 Millennium Park 41766 1564881.5100000026 37.46783292630376 Clark St & Elm St 38767 645040.0900000018 16.63889622617179 Theater on the Lake 36192 1164563.0300000026 32.17736046640149 Wells St & Elm St 35843 515079.8300000004 14.370444159250075 Kingsbury St & Kinzie St 31960 354071.70999999985 11.078589173967455 Wabash Ave & Grand Ave 31900 903143.0100000015 28.311693103448324 Clark St & Lincoln Ave 31875 626099.5900000009 19.6423400784314 Clark St & Armitage Ave 30949 632637.4799999996 20.441289863969743 Dearborn St & Erie St 30748 557442.9099999999 18.129403863665928 St. Clair St & Erie St 29630 648528.9900000002 21.887579817752286 Broadway & Barry Ave 29537 514406.78000000014 17.415674577648378 Wells St & Huron St 29038 388994.2299999999 13.396040705282731 Indiana Ave & Roosevelt Rd 28236 801545.3600000005 28.387355149454613 Larrabee St & Webster Ave 26885 416982.57000000065 15.509859401153083 Green St & Madison St 26629 396055.2700000002 14.873080851703039 New St & Illinois St 26400 636922.5000000003 24.125852272727286 Shedd Aquarium 26375 856889.0399999984 32.48868398104259 Wilton Ave & Belmont Ave 26135 426513.66000000003 16.319634972259422 Wells St & Evergreen Ave 25602 399349.3200000001 15.598364190297637 Fairbanks Ct & Grand Ave 25155 659252.4599999998 26.207611210494925 Michigan Ave & Lake St 24818 743456.460000001 29.95634055927154 LaSalle St & Illinois St 24316 484327.9699999992 19.918077397598257 Michigan Ave & Washington St 24160 674777.5599999995 27.929534768211898 Clark St & Wrightwood Ave 24128 426639.8499999989 17.682354525862024 Lakeview Ave & Fullerton Pkwy 24079 503937.4299999991 20.928503260102126 Clinton St & Madison St 24003 371847.7699999999 15.491720618256048 Wells St & Hubbard St 23686 351102.8199999997 14.823221312167513 Ashland Ave & Division St 23662 385087.62000000017 16.27451694700364 Lincoln Ave & Fullerton Ave 23463 347118.9099999994 14.794310616715654 Dearborn Pkwy & Delaware Pl 23425 404395.2799999999 17.263405763073635 Clark St & Drummond Pl 23110 400261.1700000001 17.31982561661619 Sheffield Ave & Waveland Ave 23106 498103.23 21.55731108802908 Desplaines St & Kinzie St 22891 295388.0999999994 12.904115154427478 Wabash Ave & Roosevelt Rd 22724 526628.0600000008 23.174971835944408 Clark St & Newport St 22082 380333.82 17.223703468888687 Lake Shore Dr & Wellington Ave 21936 535947.7300000009 24.43233634208611 Lake Shore Dr & Diversey Pkwy 21841 522050.36999999854 23.902310791630352 Halsted St & Roscoe St 21813 366720.15000000026 16.811999724934683 Lake Shore Dr & Belmont Ave 21776 575235.52 26.416032329169727 Clark St & Schiller St 21284 401949.1800000003 18.885039466265752 Damen Ave & Pierce Ave 20930 393698.5400000001 18.81025035833732 State St & Kinzie St 20824 462779.2199999999 22.223358624663845 Green St & Randolph St 20795 341662.29 16.430021158932433 Lake Shore Dr & Ohio St 20697 622434.2500000003 30.073645939024995 Broadway & Cornelia Ave 20420 380588.4599999996 18.63802448579822 Broadway & Waveland Ave 20409 314159.0799999999 15.393163800284183 Morgan St & Lake St 20291 332317.6199999999 16.377587107584638 Rush St & Cedar St 20225 405802.4200000002 20.06439653893697 Bissell St & Armitage Ave 19983 293964.82000000007 14.710745133363362 Clinton St & Washington Blvd 19968 264970.90000000014 13.269776642628212 McClurg Ct & Erie St 19927 433007.10000000056 21.729668289255812 Rush St & Superior St 19861 408369.74000000034 20.561388651125338 Southport Ave & Roscoe St 19811 323246.76 16.316529200948967 Pine Grove Ave & Waveland Ave 19609 453399.78999999963 23.12202509051964 State St & Randolph St 19436 501078.6

**Based on age of the rider at time of the ride**

In [0]:
trips = trips_df.join(riders_df.select('rider_id', 'birthday'), on='rider_id', how='left')
trips = trips.withColumn("age_at_ride", (F.datediff(F.col('start_at'), F.col("birthday")) / 365).cast('int'))

trips.groupBy('rider_id',"age_at_ride").agg(F.count('trip_id').alias('total_trips'),
                                             F.sum('duration_mins').alias('total_duration_mins'), 
                                             F.avg('duration_mins').alias('avg_duration_mins'))\
                                                 .orderBy(F.desc('total_trips')).display()



rider_id age_at_ride total_trips total_duration_mins avg_duration_mins 53044 38 1620 56901.78000000003 35.124555555555574 37388 16 1529 56368.34000000003 36.86614780902553 33748 25 1525 51332.12000000002 33.66040655737706 21973 32 1490 45344.83 30.43277181208054 5211 66 1422 51593.280000000006 36.282194092827005 66814 43 1396 53527.72999999998 38.343646131805144 4193 19 1367 48226.41000000001 35.27901243599123 19330 17 1359 50279.11999999998 36.99714495952905 43849 34 1346 45688.3 33.94375928677563 55633 43 1329 48944.76999999999 36.82826937547027 6048 44 1328 50434.20000000001 37.97756024096386 55730 26 1320 48487.55000000002 36.73299242424244 3876 39 1316 47584.23999999999 36.15823708206686 41323 22 1315 49843.740000000005 37.90398479087453 53843 34 1311 102368.05000000005 78.08394355453855 62636 55 1306 47876.780000000006 36.6590964777948 9465 35 1306 44582.17000000001 34.13642419601839 40407 31 1302 46658.52999999997 35.83604454685098 36271 43 1298 49964.580000000016 38.49351309707243 17421 41 1296 54331.31000000001 41.922307098765444 67878 23 1294 49211.46999999999 38.03050231839257 75203 24 1287 54231.899999999994 42.13822843822843 39417 39 1284 42219.80000000001 32.881464174454834 20322 38 1282 48508.41 37.83807332293292 1484 18 1281 58003.779999999984 45.28007806401248 67990 28 1279 44881.5 35.09108678655199 75713 30 1271 44327.47999999998 34.87606608969314 72502 25 1267 43573.500000000015 34.39108129439622 31759 25 1263 86260.97000000002 68.29847189231988 54174 19 1258 22225.690000000002 17.66748012718601 37486 33 1258 50724.85000000002 40.321820349761545 40166 38 1257 44213.77999999998 35.174049323786775 13618 28 1255 45919.36 36.58913147410359 69815 27 1236 52772.01 42.69580097087379 27866 46 1234 18763.230000000007 15.20521069692059 18930 35 1224 43427.3 35.47982026143791 42999 40 1224 50826.28000000001 41.524738562091514 8086 29 1213 69437.95000000001 57.244806265457555 51288 27 1209 32062.430000000008 26.51979321753516 25526 26 1199 43298.51000000002 36.11218515429526 40666 16 1195 47688.98000000001 39.907096234309634 14988 28 1195 44019.22 36.83616736401674 45171 35 1191 42570.27 35.74329974811083 31710 30 1186 40992.59 34.56373524451939 47029 24 1185 28259.48000000001 23.84766244725739 14363 25 1173 24068.289999999997 20.51857630008525 54803 49 1160 40882.61000000002 35.24362931034484 75677 23 1151 22936.64 19.927576020851433 52706 35 1149 41281.29 35.928015665796345 55312 33 1147 41919.58000000002 36.54714908456846 25603 46 1112 20943.159999999993 18.83377697841726 30407 23 1105 17869.229999999996 16.171248868778278 75779 28 1101 32298.629999999997 29.335722070844685 4083 20 1097 40248.29000000001 36.689416590701924 53390 34 1081 40492.929999999986 37.45876965772432 7126 36 1081 26784.37999999999 24.77740980573542 15844 27 1080 43436.280000000006 40.21877777777778 11243 42 1074 26175.70000000001 24.3721601489758 51659 53 1068 15828.71 14.820889513108613 44888 23 1064 42156.02000000002 39.620319548872196 67678 22 1062 38116.18999999999 35.890951035781534 39694 20 1060 16972.110000000008 16.011424528301895 10307 20 1045 20229.43 19.358306220095695 55028 24 1035 18939.449999999997 18.298985507246375 17989 46 1029 16253.820000000003 15.79574344023324 25890 46 1020 34531.48 33.85439215686275 33562 48 1018 20973.43999999999 20.602593320235748 7061 19 1017 26018.350000000002 25.583431661750247 1554 26 1014 20684.740000000005 20.399151873767263 14915 22 1012 13857.420000000002 13.69310276679842 30514 19 1005 34815.840000000004 34.642626865671645 51115 28 1003 23726.520000000004 23.655553339980063 12654 25 1003 14399.949999999999 14.356879361914256 14220 35 995 27116.46000000001 27.252723618090464 39077 34 991 28909.200000000008 29.171745711402632 70418 21 987 14593.55 14.785764944275583 70607 46 987 14341.760000000004 14.530658561296864 25626 27 986 31846.08000000001 32.29825557809332 18172 19 985 21392.890000000003 21.718670050761425 59788 48 980 25929.130000000005 26.45829591836735 43391 27 980 14920.29 15.224785714

**Based on whether the rider is a member or a casual rider**

In [0]:
trips_df_alias = trips_df.alias("t")
riders_df_alias = riders_df.alias("r")


result_df = trips_df_alias.join(
    riders_df_alias,
    on=F.col("t.rider_id") == F.col("r.rider_id"),
    how="left"
).groupBy("r.IsMember") \
 .agg(
     F.count("t.trip_id").alias("total_trips"),
     F.sum("t.duration_mins").alias("total_duration_mins"),
     F.avg("t.duration_mins").alias("avg_duration_mins")
 ).orderBy(F.desc("total_trips"))


result_df.display()

IsMember total_trips total_duration_mins avg_duration_mins Rider 3666306 8.030832290000041E7 21.904424480662662 Casual 918615 1.9588350399999835E7 21.323786787718287

# Analyze how much money is spent
- Per month, quarter, year
- Per member, based on the age of the rider at account start

In [0]:
#Spent per rider
payments_df.groupBy("rider_id").agg(F.sum("amount").alias("total_amount")).orderBy(F.desc("total_amount")).display()



rider_id total_amount 65089 1658.8299999999995 63569 1608.2999999999997 11368 1600.8999999999999 19270 1594.4699999999996 39136 1586.0099999999986 51831 1584.7500000000002 38365 1580.88 7243 1571.3000000000002 20017 1568.9899999999996 60682 1567.5500000000006 7555 1563.45 51610 1557.4699999999996 14523 1556.3999999999994 65498 1556.1399999999994 7254 1554.1200000000006 18292 1549.7299999999996 48580 1548.6499999999996 24070 1545.0200000000004 14319 1543.2600000000002 16462 1540.73 65138 1536.2300000000012 38813 1535.8699999999992 24873 1534.5199999999998 22158 1530.4499999999994 1101 1530.2000000000003 33267 1528.0100000000004 46990 1526.7399999999993 35401 1524.2 28624 1519.7299999999993 49163 1517.7700000000002 26204 1516.3399999999995 31578 1515.5300000000002 43719 1511.4900000000002 30419 1510.4099999999999 31552 1508.16 75860 1507.2500000000005 3113 1507.1899999999987 25353 1506.1000000000004 6625 1504.2100000000005 22100 1503.81 62729 1503.6799999999992 59759 1502.53 29504 1502.0499999999997 58332 1500.6900000000003 51713 1500.6099999999997 7074 1498.4199999999992 56504 1498.13 17404 1495.7899999999997 36295 1494.5699999999988 40202 1493.9000000000003 8540 1492.6400000000003 65663 1489.6799999999998 68837 1487.96 70965 1486.39 1098 1484.51 68062 1484.38 69644 1481.4700000000005 67723 1479.9099999999994 42322 1479.4999999999998 3793 1478.9900000000007 55485 1477.6599999999999 22755 1476.4999999999995 21034 1475.81 18824 1474.5699999999995 58012 1473.5300000000004 51176 1472.6099999999997 25723 1471.9599999999996 7222 1471.7699999999995 4834 1470.6500000000003 71332 1469.3100000000004 28750 1467.920000000001 49883 1466.7499999999995 73973 1465.2999999999997 21198 1464.9500000000007 40161 1464.65 2260 1461.5200000000011 61085 1460.9700000000005 35940 1459.0900000000001 21785 1458.9000000000003 47295 1458.7299999999996 36469 1458.2700000000002 56437 1457.4000000000003 21599 1456.45 32634 1455.8700000000003 3154 1455.39 61559 1455.1400000000003 29744 1453.4999999999998 60943 1453.3899999999999 36150 1452.4699999999998 50845 1452.3300000000002 7967 1451.789999999999 69594 1451.5800000000002 7063 1451.0900000000006 55926 1448.1100000000004 48546 1447.9800000000002 8657 1445.7100000000003 17905 1445.7000000000003 26182 1444.8900000000006 73024 1444.8000000000004 49813 1442.3300000000008 75178 1442.2199999999998 13993 1441.85 10648 1441.5699999999997 54127 1441.4899999999996 16400 1440.6499999999999 26210 1439.5800000000002 26571 1439.53 2502 1439.5200000000002 23351 1438.47 31460 1437.9999999999989 50051 1436.1999999999998 64075 1435.6499999999999 13834 1432.4400000000003 58065 1432.43 73541 1430.7700000000004 74390 1430.2299999999996 73276 1429.8499999999997 65543 1427.5500000000002 65996 1427.1200000000001 18899 1426.650000000001 16984 1426.4699999999993 1072 1424.74 19663 1424.74 41814 1424.5699999999995 4151 1421.9 48643 1421.17 9921 1420.3200000000002 24595 1419.69 57438 1419.48 12104 1419.1600000000005 23537 1417.5599999999997 9454 1416.8300000000004 10631 1416.3700000000006 43187 1415.4900000000005 63944 1414.4900000000002 7931 1413.8999999999999 64030 1413.1 23434 1411.1600000000003 37660 1410.8500000000004 52439 1409.99 37516 1407.8900000000003 32003 1407.5599999999995 47120 1407.48 13787 1405.8600000000006 25483 1405.5000000000002 51442 1403.67 59973 1403.1100000000008 65357 1402.4700000000012 48083 1401.71 30813 1400.9500000000005 28887 1400.2700000000002 51195 1400.0600000000004 52919 1399.67 21277 1399.0699999999997 44778 1397.4800000000007 30994 1397.07 40425 1396.8499999999997 45576 1396.2800000000007 36051 1393.9199999999996 20592 1392.9399999999994 21834 1392.7999999999995 34366 1392.1400000000006 67899 1392.0699999999995 70421 1391.58 30650 1391.4900000000005 57459 1390.4 4206 1390.1400000000003 16363 1389.2800000000004 22077 1387.2800000000002 42942 1387.2300000000012 43420 1386.3300000000004 38271 1382.3399999999995 47243 1381.35 63703 1380.5900000000006 51964 1380.1700000000003 9400 1380.1499999999996 58838 

In [0]:
payments_df.groupBy(F.year("date"). alias('year')).agg(F.sum("amount").alias("total_amount")).orderBy(F.desc("total_amount")).display()

year total_amount 2021 6081098.249999979 2020 4315449.400000015 2019 2978658.7900000038 2018 2000105.500000001 2017 1308372.5399999977 2022 1189970.4499999983 2016 825120.8099999988 2015 477233.21999999986 2014 227402.94999999995 2013 53693.34000000001

In [0]:
payments_df.groupBy(F.quarter("date"). alias('quarter')).agg(F.sum("amount").alias("total_amount")).orderBy(F.asc("quarter")).display()

quarter total_amount 1 5112376.490000002 2 4328269.550000012 3 4773199.860000011 4 5243259.349999996

In [0]:
payments_df.groupBy(F.month("date"). alias('month')).agg(F.sum("amount").alias("total_amount")).orderBy(F.asc("month")).display()

month total_amount 1 1855786.829999999 2 1907807.2700000014 3 1348782.389999997 4 1395762.7800000007 5 1441279.1899999976 6 1491227.5799999991 7 1538960.88 8 1592322.5800000012 9 1641916.4000000013 10 1696207.3200000029 11 1747273.5699999984 12 1799778.4600000016

In [0]:
payments_df.groupBy(F.year("date"). alias('year'), F.quarter("date"). alias('quarter'), F.month("date"). alias('month')).agg(F.sum("amount").alias("total_amount")).orderBy(F.asc("year"), F.asc('quarter')).display()

year quarter month total_amount 2013 1 2 12.9 2013 1 3 817.7499999999999 2013 2 5 2716.71 2013 2 4 1672.65 2013 2 6 3775.3 2013 3 9 6672.100000000001 2013 3 8 5834.3 2013 3 7 4760.959999999999 2013 4 11 9195.449999999999 2013 4 12 10349.1 2013 4 10 7886.120000000001 2014 1 1 11471.64 2014 1 2 12584.920000000002 2014 1 3 13385.36 2014 2 4 15351.430000000004 2014 2 6 18110.54 2014 2 5 16802.17 2014 3 9 22526.93 2014 3 8 20891.41 2014 3 7 19542.469999999994 2014 4 11 25637.65 2014 4 12 27121.500000000007 2014 4 10 23976.93 2015 1 3 32937.54000000001 2015 1 1 29358.36 2015 1 2 30737.8 2015 2 5 36222.009999999995 2015 2 6 38474.240000000005 2015 2 4 34633.600000000006 2015 3 9 44319.0 2015 3 7 40391.19 2015 3 8 42372.860000000015 2015 4 10 46530.67 2015 4 11 49472.97 2015 4 12 51782.979999999996 2016 1 2 56950.98999999999 2016 1 1 53699.490000000005 2016 1 3 59070.32000000001 2016 2 4 61724.05000000002 2016 2 5 64487.999999999985 2016 2 6 67136.98999999996 2016 3 7 69651.27 2016 3 9 74731.56000000003 2016 3 8 73114.18999999997 2016 4 11 81474.83999999998 2016 4 12 84826.91000000002 2016 4 10 78252.2 2017 1 2 91394.28000000003 2017 1 3 94633.50000000003 2017 1 1 88281.70000000004 2017 2 4 98854.39999999997 2017 2 6 105314.51000000001 2017 2 5 101697.06000000001 2017 3 8 114747.01999999993 2017 3 9 119356.84 2017 3 7 109724.12999999999 2017 4 11 128260.06000000006 2017 4 10 123272.42999999993 2017 4 12 132836.61000000004 2018 1 2 142420.53999999992 2018 1 3 147189.96999999997 2018 1 1 137418.30000000008 2018 2 6 163802.63999999993 2018 2 5 158103.36 2018 2 4 152000.09000000003 2018 3 7 167911.17000000004 2018 3 8 175022.62999999995 2018 3 9 179484.00999999995 2018 4 10 186141.85000000006 2018 4 11 191941.43000000017 2018 4 12 198669.51 2019 1 3 219597.40999999997 2019 1 2 213286.69999999995 2019 1 1 206395.33999999997 2019 2 5 234522.3600000001 2019 2 4 227701.01000000015 2019 2 6 243091.5000000003 2019 3 9 268256.09 2019 3 7 251532.5300000001 2019 3 8 258662.85999999993 2019 4 10 276125.49000000005 2019 4 11 285230.12 2019 4 12 294257.37999999983 2020 1 2 313517.49999999994 2020 1 3 322366.36999999976 2020 1 1 303771.75999999995 2020 2 5 341008.2700000002 2020 2 4 332073.88999999984 2020 2 6 351315.21000000037 2020 3 7 362433.4899999994 2020 3 9 385576.3400000005 2020 3 8 374396.5499999999 2020 4 12 420704.5499999996 2020 4 11 409920.4400000002 2020 4 10 398365.0299999998 2021 1 1 434891.0599999997 2021 1 2 447430.3699999997 2021 1 3 458784.17000000004 2021 2 5 485719.2500000001 2021 2 6 500206.6500000005 2021 2 4 471751.65999999945 2021 3 7 513013.67000000016 2021 3 8 527280.7599999998 2021 3 9 540993.5299999994 2021 4 12 579229.92 2021 4 10 555656.6 2021 4 11 566140.6100000006 2022 1 1 590499.1800000003 2022 1 2 599471.27

### EXTRA CREDIT - Analyze how much money is spent per member
- Based on how many rides the rider averages per month
- Based on how many minutes the rider spends on a bike per month

In [0]:
payments_df.groupBy('rider_id').agg(F.avg("amount").alias("average_amount"), F.sum("amount").alias("total_amount")).orderBy(F.desc("total_amount")).display()

rider_id average_amount total_amount 65089 15.503084112149528 1658.8299999999995 63569 15.317142857142855 1608.2999999999997 11368 14.961682242990653 1600.8999999999999 19270 15.480291262135918 1594.4699999999996 39136 14.962358490566025 1586.0099999999986 51831 14.810747663551403 1584.7500000000002 38365 15.056000000000001 1580.88 7243 14.549074074074076 1571.3000000000002 20017 15.086442307692304 1568.9899999999996 60682 14.788207547169817 1567.5500000000006 7555 14.611682242990655 1563.45 51610 15.121067961165044 1557.4699999999996 14523 14.822857142857137 1556.3999999999994 65498 14.543364485981304 1556.1399999999994 7254 14.801142857142862 1554.1200000000006 18292 14.901249999999996 1549.7299999999996 48580 14.890865384615381 1548.6499999999996 24070 14.439439252336452 1545.0200000000004 14319 15.279801980198021 1543.2600000000002 16462 14.26601851851852 1540.73 65138 14.771442307692318 1536.2300000000012 38813 14.627333333333326 1535.8699999999992 24873 14.208518518518517 1534.5199999999998 22158 14.170833333333327 1530.4499999999994 1101 14.300934579439256 1530.2000000000003 33267 14.552476190476195 1528.0100000000004 46990 14.268598130841115 1526.7399999999993 35401 14.112962962962964 1524.2 28624 14.337075471698107 1519.7299999999993 49163 15.48744897959184 1517.7700000000002 26204 15.163399999999994 1516.3399999999995 31578 14.032685185185187 1515.5300000000002 43719 14.67466019417476 1511.4900000000002 30419 14.249150943396225 1510.4099999999999 31552 14.932277227722773 1508.16 75860 15.22474747474748 1507.2500000000005 3113 14.354190476190464 1507.1899999999987 25353 14.208490566037739 1506.1000000000004 6625 14.058037383177576 1504.2100000000005 22100 13.924166666666666 1503.81 62729 14.053084112149525 1503.6799999999992 59759 14.309809523809523 1502.53 29504 14.871782178217819 1502.0499999999997 58332 14.429711538461541 1500.6900000000003 51713 14.291523809523806 1500.6099999999997 7074 14.13603773584905 1498.4199999999992 56504 14.405096153846156 1498.13 17404 14.664607843137253 1495.7899999999997 36295 14.23399999999999 1494.5699999999988 40202 14.503883495145635 1493.9000000000003 8540 14.352307692307695 1492.6400000000003 65663 14.749306930693068 1489.6799999999998 68837 14.17104761904762 1487.96 70965 14.156095238095238 1486.39 1098 14.274134615384614 1484.51 68062 14.136952380952382 1484.38 69644 14.668019801980202 1481.4700000000005 67723 14.22990384615384 1479.9099999999994 42322 13.957547169811319 1479.4999999999998 3793 13.694351851851858 1478.9900000000007 55485 15.392291666666665 1477.6599999999999 22755 13.929245283018863 1476.4999999999995 21034 14.611980198019802 1475.81 18824 13.911037735849051 1474.5699999999995 58012 14.735300000000004 1473.5300000000004 51176 14.437352941176467 1472.6099999999997 25723 14.018666666666663 1471.9599999999996 7222 13.627499999999996 1471.7699999999995 4834 14.855050505050508 1470.6500000000003 71332 14.127980769230772 1469.3100000000004 28750 13.59185185185186 1467.920000000001 49883 14.81565656565656 1466.7499999999995 73973 14.089423076923074 1465.2999999999997 21198 13.820283018867931 1464.9500000000007 40161 14.501485148514853 1464.65 2260 14.053076923076933 1461.5200000000011 61085 14.047788461538467 1460.9700000000005 35940 14.888673469387756 1459.0900000000001 21785 14.444554455445548 1458.9000000000003 47295 14.442871287128709 1458.7299999999996 36469 14.157961165048546 1458.2700000000002 56437 13.880000000000003 1457.4000000000003 21599 13.48564814814815 1456.45 32634 13.998750000000003 1455.8700000000003 3154 13.994134615384617 1455.39 61559 14.40732673267327 1455.1400000000003 29744 14.391089108910888 1453.4999999999998 60943 14.5339 1453.3899999999999 36150 14.239901960784312 1452.4699999999998 50845 13.701226415094341 1452.3300000000002 7967 13.568130841121487 1451.789999999999 69594 14.093009708737865 1451.5800000000002 7063 14.95969072164949 1451.0900000000006 55926 14.776632653061228 1448.1100000000004 48546 15.083125000000003 1447.9800000000002 86

In [0]:
payments_df.groupBy('rider_id', F.month("date"). alias('month')).agg(F.avg("amount").alias("average_amount")).orderBy(("rider_id")).display()

rider_id month average_amount 1000 2 9.0 1000 12 9.0 1000 7 9.0 1000 10 9.0 1000 5 9.0 1000 3 9.0 1000 9 9.0 1000 8 9.0 1000 6 9.0 1000 4 9.0 1000 1 9.0 1000 11 9.0 1001 1 9.0 1001 3 9.0 1001 2 9.0 1001 7 9.0 1001 12 9.0 1001 4 9.0 1001 8 9.0 1001 6 9.0 1001 5 9.0 1001 9 9.0 1003 1 16.26 1003 11 12.816666666666668 1003 8 17.165 1003 4 17.695 1003 5 18.79 1003 7 7.97 1003 2 10.58 1003 6 13.91 1003 10 16.006666666666668 1003 3 14.969999999999999 1003 12 7.963333333333334 1003 9 13.063333333333333 1004 2 9.0 1004 7 9.0 1004 5 9.0 1004 11 9.0 1004 12 9.0 1004 1 9.0 1004 10 9.0 1004 4 9.0 1004 8 9.0 1004 6 9.0 1004 9 9.0 1004 3 9.0 1005 10 11.455 1005 2 12.895000000000001 1005 9 16.5 1005 1 13.25 1005 3 9.46 1005 12 9.26 1005 6 19.815 1005 7 21.259999999999998 1005 8 17.15 1005 4 12.59 1005 11 19.880000000000003 1005 5 7.51 1006 9 9.0 1006 8 9.0 1006 12 9.0 1006 5 9.0 1006 4 9.0 1006 2 9.0 1006 7 9.0 1006 10 9.0 1006 3 9.0 1006 1 9.0 1006 11 9.0 1006 6 9.0 1007 4 16.256 1007 10 12.898 1007 2 14.75 1007 9 11.200000000000001 1007 12 14.434000000000001 1007 6 16.330000000000002 1007 11 10.041999999999998 1007 7 16.938000000000002 1007 3 11.110000000000001 1007 5 14.27 1007 1 11.263333333333334 1007 8 14.024000000000001 1008 5 9.0 1008 7 9.0 1008 4 9.0 1008 6 9.0 1009 1 9.0 1009 11 9.0 1009 7 9.0 1009 3 9.0 1009 4 9.0 1009 6 9.0 1009 10 9.0 1009 2 9.0 1009 5 9.0 1009 9 9.0 1009 8 9.0 1009 12 9.0 1010 8 9.0 1010 2 9.0 1010 1 9.0 1010 9 9.0 1010 11 9.0 1010 4 9.0 1010 12 9.0 1010 7 9.0 1010 6 9.0 1010 5 9.0 1010 3 9.0 1010 10 9.0 1011 6 9.0 1011 7 9.0 1011 8 9.0 1011 2 9.0 1011 5 9.0 1011 9 9.0 1011 11 9.0 1011 4 9.0 1011 3 9.0 1011 1 9.0 1011 12 9.0 1011 10 9.0 1012 1 9.0 1012 2 9.0 1012 11 9.0 1012 12 9.0 1013 10 9.0 1013 11 9.0 1013 8 9.0 1013 2 9.0 1013 7 9.0 1013 4 9.0 1013 5 9.0 1013 3 9.0 1013 9 9.0 1013 1 9.0 1013 6 9.0 1014 11 9.0 1014 10 9.0 1014 2 9.0 1014 12 9.0 1014 5 9.0 1014 6 9.0 1014 9 9.0 1014 3 9.0 1014 4 9.0 1014 7 9.0 1014 8 9.0 1014 1 9.0 1015 7 9.0 1015 2 9.0 1015 12 9.0 1015 1 9.0 1015 11 9.0 1015 6 9.0 1015 3 9.0 1015 5 9.0 1015 9 9.0 1015 4 9.0 1015 8 9.0 1015 10 9.0 1017 1 9.0 1017 7 9.0 1017 4 9.0 1017 10 9.0 1017 6 9.0 1017 2 9.0 1017 9 9.0 1017 5 9.0 1017 12 9.0 1017 3 9.0 1017 11 9.0 1017 8 9.0 1018 9 22.35 1018 10 21.64 1018 1 22.76 1018 2 8.14 1018 8 23.55 1018 12 20.63 1018 11 4.69 1019 8 20.51 1019 11 7.86 1019 9 7.19 1019 10 12.52 1019 12 11.14 1019 1 16.6 1020 10 9.0 1020 8 9.0 1020 7 9.0 1020 4 9.0 1020 11 9.0 1020 3 9.0 1020 5 9.0 1020 6 9.0 1020 9 9.0 1020 2 9.0 1020 1 9.0 1020 12 9.0 1021 2 11.145 1021 10 10.466666666666667 1021 12 8.545 1021 11 10.186666666666667 1021 9 5.85 1021 4 18.345 1021 7 20.895 1021 8 15.615 1021 6 17.509999999999998 1021 1 15.545 1021 3 19.759999999999998 1021 5 10.6 1022 12 9.0 1022 2 9.0 1022 9 9.0 1022 1 9.0 1022 10 9.0 1022 4 9.0 1022 5 9.0 1022 7 9.0 1022 3 9.0 1022 11 9.0 1022 8 9.0 1022 6 9.0 1023 4 9.0 1023 7 9.0 1023 1 9.0 1023 12 9.0 1023 6 9.0 1023 8 9.0 1023 5 9.0 1023 2 9.0 1023 11 9.0 1023 3 9.0 1023 10 9.0 1023 9 9.0 1024 7 9.0 1024 9 9.0 1024 6 9.0 1024 2 9.0 1024 12 9.0 1024 10 9.0 1024 8 9.0 1024 4 9.0 1024 5 9.0 1024 11 9.0 1024 1 9.0 1025 11 22.395 1025 3 19.24 1025 7 8.405000000000001 1025 5 17.99 1025 10 13.209999999999999 1025 9 22.84 1025 1 18.99 1025 8 13.645 1025 4 7.43 1025 6 10.655000000000001 1025 12 20.93 1025 2 17.2 1026 1 9.0 1026 12 9.0 1026 2 9.0 1027 1 12.65 1027 12 18.14 1027 2 16.61 1028 3 20.674999999999997 1028 2 12.386666666666668 1028 4 19.060000000000002 1028 1 9.08 1028 5 12.85 1028 7 12.865 1028 11 10.75 1028 6 18.175 1028 12 18.88 1028 9 14.385000000000002 1028 8 8.315000000000001 1028 10 14.926666666666668 1029 2 3.13 1029 11 15.25 1029 12 8.03 1029 1 11.16 1029 5 7.39 1029 6 3.28 1029 7 17.83 1029 4 16.14 1029 8 8.09 1029 3 12.49 1030 7 9.0 1030 9 9.0 1030 6 9.0 1030 2 9.0 1030 1 9.0 1030 12 9.0 1030 3 9.0 1030 4 9.0 1030 11 9.0 1030 8 9.0 1030 5 9.0 1030 10 9.0 1031 10 9.0 1031 12 9.0 1031 2 9.0 1031 5 9.0 1031 9 9.0 1031 6